Validate VedEf Problem Compliance with ARC002 Parameter Registry.

This script demonstrates how to use the ARC002 validation utilities to check
that a Problem's parameters align with the ARC002 parameter registry.


In [ ]:
import importlib.util
import sys
from pathlib import Path

from paroto.validation.arc002 import (
    ARC002Registry,
    extract_problem_variable_names,
)

# Import the problem setup dynamically
spec = importlib.util.spec_from_file_location(
    "setup_vedef_problem", Path(__file__).parent / "1_setup_vedef_problem.py"
)
setup_module = importlib.util.module_from_spec(spec)
spec.loader.exec_module(setup_module)
setup_vedef_problem = setup_module.setup_vedef_problem


def main():
    """Validate VedEf problem against ARC002 registry."""
    print("=" * 80)
    print("VedEf Problem - ARC002 Compliance Validation")
    print("=" * 80)

    # Setup the VedEf problem
    print("\nSetting up VedEf problem...")
    prob = setup_vedef_problem()

    # Load ARC002 registry
    print("\nLoading ARC002 parameter registry...")
    registry = ARC002Registry()
    print(f"Loaded {len(registry.tags_to_equipment)} valid parameter tags from ARC002")

    # Extract all variable names from problem
    print("\nExtracting variable names from OpenMDAO problem...")
    all_vars = extract_problem_variable_names(prob)
    print(f"Found {len(all_vars)} unique variable names in problem")

    # Define the critical VedEf design parameters (ARC002 tags)
    critical_params = ["G_UMAX_OUT", "G_e", "TP_D_OUT", "G_F", "G_Ep", "TP_QM"]

    # Define expected system associations
    expected_systems = {
        "G_UMAX_OUT": "Generator",  # Generator voltage
        "G_e": "PlasmaTorch",  # Interelectrode gap
        "TP_D_OUT": "PlasmaTorch",  # Torch outlet diameter
        "G_F": "Generator",  # Pulse frequency (PRF)
        "G_Ep": "Generator",  # Energy per pulse
        "TP_QM": "PlasmaTorch",  # Mass flow rate per torch
    }

    # Validate critical parameters
    print("\n" + "=" * 80)
    print("VALIDATING CRITICAL DESIGN PARAMETERS")
    print("=" * 80)

    valid, invalid, mismatched = registry.validate_problem_parameters(
        critical_params, expected_systems
    )

    # Print detailed report
    print(f"\nCritical parameters: {len(critical_params)}")
    print(f"Valid ARC002 tags: {len(valid)}")
    print(f"Invalid tags: {len(invalid)}")
    print(f"System mismatches: {len(mismatched)}")

    if valid:
        print("\n" + "-" * 80)
        print("VALID ARC002 PARAMETERS")
        print("-" * 80)
        for tag in valid:
            equipment = registry.get_equipment_class(tag)
            description = registry.get_description(tag)
            units = registry.get_units(tag)
            print(f"\n  {tag}")
            print(f"    Equipment: {equipment}")
            print(f"    Description: {description}")
            if units and units != "/":
                print(f"    Units: {units}")

    if invalid:
        print("\n" + "-" * 80)
        print("INVALID PARAMETERS (not in ARC002)")
        print("-" * 80)
        for tag in invalid:
            print(f"  {tag}")

    if mismatched:
        print("\n" + "-" * 80)
        print("SYSTEM MISMATCHES")
        print("-" * 80)
        for msg in mismatched:
            print(f"  {msg}")

    # Summary
    print("\n" + "=" * 80)
    print("SUMMARY")
    print("=" * 80)

    if len(invalid) == 0 and len(mismatched) == 0:
        print("\n[OK] All critical parameters are ARC002-compliant!")
        print("[OK] All parameters are associated with correct Equipment_Class")
        return 0
    else:
        print("\n[FAIL] Some parameters are not ARC002-compliant")
        if invalid:
            print(f"  - {len(invalid)} parameter(s) not found in registry")
        if mismatched:
            print(f"  - {len(mismatched)} parameter(s) have incorrect system association")
        return 1


if __name__ == "__main__":
    sys.exit(main())